## This notebook provides some simple illustrations to the course Many-body physics and quantum computation, delivered by Kareljan Schoutens at the GGI SFT 2022 PhD School, February 2022

### Goal: illustration of VQE with Hamiltonian Variational Ansatz (HVA) for XXX chain

## Start with $L=4$

In [1]:
import cirq
import numpy as np

length=4

qubits = cirq.LineQubit.range(length)

pauliX = cirq.X
pauliY = cirq.Y
pauliZ = cirq.Z

print(qubits)
print()

Heis_ham: cirq.ops.PauliSum = sum(pauliX(qubits[k - 1]) * pauliX(qubits[k]) 
+ pauliY(qubits[k - 1]) * pauliY(qubits[k]) + pauliZ(qubits[k - 1]) * pauliZ(qubits[k]) for k in range(length))
    
print("Hamiltonian =", Heis_ham)


[cirq.LineQubit(0), cirq.LineQubit(1), cirq.LineQubit(2), cirq.LineQubit(3)]

Hamiltonian = 1.000*X(0)*X(3)+1.000*Y(0)*Y(3)+1.000*Z(0)*Z(3)+1.000*X(0)*X(1)+1.000*Y(0)*Y(1)+1.000*Z(0)*Z(1)+1.000*X(1)*X(2)+1.000*Y(1)*Y(2)+1.000*Z(1)*Z(2)+1.000*X(2)*X(3)+1.000*Y(2)*Y(3)+1.000*Z(2)*Z(3)


In [2]:
circuit = cirq.Circuit()
print(circuit)

for i in range(length):
    if i % 2 == 0:
        circuit.append(cirq.H(qubits[i]))
        circuit.append(cirq.X(qubits[i]))
        circuit.append(cirq.CNOT(qubits[i],qubits[i+1]))
        circuit.append(cirq.X(qubits[i]))
        circuit.append(cirq.Z(qubits[i+1]))
    
print(circuit)

simulator = cirq.Simulator()
result = simulator.simulate(circuit, qubit_order=qubits)

# print("")
# print(result.final_state_vector)


0: ───H───X───@───X───
              │
1: ───────────X───Z───

2: ───H───X───@───X───
              │
3: ───────────X───Z───


In [3]:
expectation = Heis_ham.expectation_from_state_vector(
    result.final_state_vector,
    qubit_map={q: q.x for q in qubits})
print("xx+yy+zz expectation", expectation)

xx+yy+zz expectation (-5.999999284744263+0j)


In [4]:
"""Define the Heis gate on two qubits."""
class HeisGate(cirq.Gate):
    def __init__(self, alpha):
        super(HeisGate, self)
        self.alpha = alpha
    
    def _num_qubits_(self):
        return 2

    def _unitary_(self):
        return np.array([
            [np.exp(- 1.0j * self.alpha/2),  0.0, 0.0,  0.0],
            [0.0,  np.cos(self.alpha/2), -1.0j * np.sin(self.alpha/2),  0.0],
            [0.0,  -1.0j * np.sin(self.alpha/2), np.cos(self.alpha/2),  0.0],
            [0.0,  0.0, 0.0, np.exp(- 1.0j * self.alpha/2)]
        ])
    
    def _circuit_diagram_info_(self, args):
        return f"Heis({self.alpha})", f"Heis({self.alpha})"


In [5]:
def even_Heis_layer(length, angle):
    """Yields Heis rotations by angle on chain of given length."""
    for i in range(length):
        if i % 2 == 0:
            yield HeisGate(angle).on(cirq.LineQubit(i),cirq.LineQubit(i+1))

In [6]:
circuit.append(even_Heis_layer(length, 0.4))
print(circuit)

0: ───H───X───@───X───Heis(0.4)───
              │       │
1: ───────────X───Z───Heis(0.4)───

2: ───H───X───@───X───Heis(0.4)───
              │       │
3: ───────────X───Z───Heis(0.4)───


In [7]:
def odd_Heis_layer(length, angle):
    """Yields Heis rotations by angle on chain of given length."""
    for i in range(length):
        if i % 2 == 0:
            yield HeisGate(angle).on(cirq.LineQubit(i+1),cirq.LineQubit((i+2) % length))

In [8]:
circuit.append(odd_Heis_layer(length, 0.4))
print(circuit)

                                  ┌──────────────────┐
0: ───H───X───@───X───Heis(0.4)─────────────Heis(0.4)────
              │       │                     │
1: ───────────X───Z───Heis(0.4)────Heis(0.4)┼────────────
                                   │        │
2: ───H───X───@───X───Heis(0.4)────Heis(0.4)┼────────────
              │       │                     │
3: ───────────X───Z───Heis(0.4)─────────────Heis(0.4)────
                                  └──────────────────┘


In [9]:
result = simulator.simulate(circuit, qubit_order=qubits)

expectation = Heis_ham.expectation_from_state_vector(
    result.final_state_vector,
    qubit_map={q: q.x for q in qubits})
print("xx+yy+zz expectation", expectation)

xx+yy+zz expectation (-5.090119659900665+0j)


### HVA with two layers, parameters alpha, beta

In [10]:
alpha_opt=0
beta_opt=0

expectation_opt=-3.0*length/2

num_step=20

for i1 in range(num_step+1):
    for i2 in range(num_step+1):
            alpha=np.pi*i1/(2*num_step)
            beta=np.pi*i2/(2*num_step)
            
            circuit = cirq.Circuit()

            for i in range(length):
                if i % 2 == 0:
                    circuit.append(cirq.H(qubits[i]))
                    circuit.append(cirq.X(qubits[i]))
                    circuit.append(cirq.CNOT(qubits[i],qubits[i+1]))
                    circuit.append(cirq.X(qubits[i]))
                    circuit.append(cirq.Z(qubits[i+1]))

            circuit.append(odd_Heis_layer(length, alpha))
            circuit.append(even_Heis_layer(length, beta))
            
            result = simulator.simulate(circuit, qubit_order=qubits)
            # print(result.final_state_vector)
            # print("")

            expectation = np.real(Heis_ham.expectation_from_state_vector(
            result.final_state_vector,
                qubit_map={q: q.x for q in qubits}))
            print(np.around(alpha,4), "  ", np.around(beta,4),"   xx+yy+zz expectation", np.around(expectation,6))
            # print("xx+yy+zz expectation", expectation)
            
            if expectation < expectation_opt:
                alpha_opt=alpha
                beta_opt=beta
                expectation_opt=expectation

0.0    0.0    xx+yy+zz expectation -5.999999
0.0    0.0785    xx+yy+zz expectation -5.999999
0.0    0.1571    xx+yy+zz expectation -5.999998
0.0    0.2356    xx+yy+zz expectation -5.999999
0.0    0.3142    xx+yy+zz expectation -5.999999
0.0    0.3927    xx+yy+zz expectation -5.999998
0.0    0.4712    xx+yy+zz expectation -5.999999
0.0    0.5498    xx+yy+zz expectation -5.999999
0.0    0.6283    xx+yy+zz expectation -5.999999
0.0    0.7069    xx+yy+zz expectation -5.999999
0.0    0.7854    xx+yy+zz expectation -5.999999
0.0    0.8639    xx+yy+zz expectation -5.999999
0.0    0.9425    xx+yy+zz expectation -5.999999
0.0    1.021    xx+yy+zz expectation -5.999999
0.0    1.0996    xx+yy+zz expectation -5.999999
0.0    1.1781    xx+yy+zz expectation -5.999999
0.0    1.2566    xx+yy+zz expectation -5.999999
0.0    1.3352    xx+yy+zz expectation -5.999999
0.0    1.4137    xx+yy+zz expectation -5.999999
0.0    1.4923    xx+yy+zz expectation -5.999999
0.0    1.5708    xx+yy+zz expectation -5.999

0.6283    0.1571    xx+yy+zz expectation -4.859456
0.6283    0.2356    xx+yy+zz expectation -5.335332
0.6283    0.3142    xx+yy+zz expectation -5.802051
0.6283    0.3927    xx+yy+zz expectation -6.248122
0.6283    0.4712    xx+yy+zz expectation -6.662563
0.6283    0.5498    xx+yy+zz expectation -7.035168
0.6283    0.6283    xx+yy+zz expectation -7.356763
0.6283    0.7069    xx+yy+zz expectation -7.619427
0.6283    0.7854    xx+yy+zz expectation -7.816694
0.6283    0.8639    xx+yy+zz expectation -7.943707
0.6283    0.9425    xx+yy+zz expectation -7.997339
0.6283    1.021    xx+yy+zz expectation -7.976267
0.6283    1.0996    xx+yy+zz expectation -7.881011
0.6283    1.1781    xx+yy+zz expectation -7.713918
0.6283    1.2566    xx+yy+zz expectation -7.479102
0.6283    1.3352    xx+yy+zz expectation -7.182343
0.6283    1.4137    xx+yy+zz expectation -6.830949
0.6283    1.4923    xx+yy+zz expectation -6.433572
0.6283    1.5708    xx+yy+zz expectation -5.999999
0.7069    0.0    xx+yy+zz expect

1.1781    1.4137    xx+yy+zz expectation -6.530195
1.1781    1.4923    xx+yy+zz expectation -6.30032
1.1781    1.5708    xx+yy+zz expectation -5.999998
1.2566    0.0    xx+yy+zz expectation -0.572949
1.2566    0.0785    xx+yy+zz expectation -0.882207
1.2566    0.1571    xx+yy+zz expectation -1.250665
1.2566    0.2356    xx+yy+zz expectation -1.669252
1.2566    0.3142    xx+yy+zz expectation -2.127661
1.2566    0.3927    xx+yy+zz expectation -2.614602
1.2566    0.4712    xx+yy+zz expectation -3.118088
1.2566    0.5498    xx+yy+zz expectation -3.62572
1.2566    0.6283    xx+yy+zz expectation -4.125
1.2566    0.7069    xx+yy+zz expectation -4.603631
1.2566    0.7854    xx+yy+zz expectation -5.049829
1.2566    0.8639    xx+yy+zz expectation -5.452609
1.2566    0.9425    xx+yy+zz expectation -5.80205
1.2566    1.021    xx+yy+zz expectation -6.08955
1.2566    1.0996    xx+yy+zz expectation -6.308028
1.2566    1.1781    xx+yy+zz expectation -6.452107
1.2566    1.2566    xx+yy+zz expectation -

In [11]:
print("alpha_opt=",np.around(alpha_opt,4),"  beta_opt=",np.around(beta_opt,4))
print()
print("Best estimate for GS energy after first iteration", np.around(expectation_opt,8))

alpha_opt= 0.6283   beta_opt= 0.9425

Best estimate for GS energy after first iteration -7.99733853


In [12]:
print("alpha_opt=",alpha_opt/np.pi,"pi,   beta_opt=",beta_opt/np.pi,"pi")

alpha_opt= 0.2 pi,   beta_opt= 0.3 pi


### Two layers (p=1 cycles), 2 parameters, refine search around alpha=$\pi/5$, beta=$3 \pi/10$

In [13]:
alpha_opt=0
beta_opt=0

expectation_opt=-3.0*length/2

num_step=20

for i1 in range(num_step+1):
    for i2 in range(num_step+1):
            alpha=np.pi/5 +np.pi*(i1-num_step/2)/(10*num_step)
            beta=3*np.pi/10 +np.pi*(i2-num_step/2)/(10*num_step)
            
            circuit = cirq.Circuit()

            for i in range(length):
                if i % 2 == 0:
                    circuit.append(cirq.H(qubits[i]))
                    circuit.append(cirq.X(qubits[i]))
                    circuit.append(cirq.CNOT(qubits[i],qubits[i+1]))
                    circuit.append(cirq.X(qubits[i]))
                    circuit.append(cirq.Z(qubits[i+1]))

            circuit.append(odd_Heis_layer(length, alpha))
            circuit.append(even_Heis_layer(length, beta))
            
            result = simulator.simulate(circuit, qubit_order=qubits)
            # print(result.final_state_vector)
            # print("")

            expectation = np.real(Heis_ham.expectation_from_state_vector(
            result.final_state_vector,
                qubit_map={q: q.x for q in qubits}))
            print(np.around(alpha,4), "  ", np.around(beta,4),"   xx+yy+zz expectation", np.around(expectation,6))
            # print("xx+yy+zz expectation", expectation)
            
            if expectation < expectation_opt:
                alpha_opt=alpha
                beta_opt=beta
                #gamma_opt=gamma
                expectation_opt=expectation

0.4712    0.7854    xx+yy+zz expectation -7.808727
0.4712    0.8011    xx+yy+zz expectation -7.826953
0.4712    0.8168    xx+yy+zz expectation -7.842764
0.4712    0.8325    xx+yy+zz expectation -7.856146
0.4712    0.8482    xx+yy+zz expectation -7.867087
0.4712    0.8639    xx+yy+zz expectation -7.875573
0.4712    0.8796    xx+yy+zz expectation -7.8816
0.4712    0.8954    xx+yy+zz expectation -7.885159
0.4712    0.9111    xx+yy+zz expectation -7.886249
0.4712    0.9268    xx+yy+zz expectation -7.884865
0.4712    0.9425    xx+yy+zz expectation -7.881011
0.4712    0.9582    xx+yy+zz expectation -7.874691
0.4712    0.9739    xx+yy+zz expectation -7.865912
0.4712    0.9896    xx+yy+zz expectation -7.854679
0.4712    1.0053    xx+yy+zz expectation -7.841006
0.4712    1.021    xx+yy+zz expectation -7.824907
0.4712    1.0367    xx+yy+zz expectation -7.806398
0.4712    1.0524    xx+yy+zz expectation -7.785493
0.4712    1.0681    xx+yy+zz expectation -7.762217
0.4712    1.0838    xx+yy+zz expec

0.5969    0.9739    xx+yy+zz expectation -7.994553
0.5969    0.9896    xx+yy+zz expectation -7.988528
0.5969    1.0053    xx+yy+zz expectation -7.979606
0.5969    1.021    xx+yy+zz expectation -7.967795
0.5969    1.0367    xx+yy+zz expectation -7.953108
0.5969    1.0524    xx+yy+zz expectation -7.935555
0.5969    1.0681    xx+yy+zz expectation -7.91516
0.5969    1.0838    xx+yy+zz expectation -7.891936
0.5969    1.0996    xx+yy+zz expectation -7.865911
0.6126    0.7854    xx+yy+zz expectation -7.830748
0.6126    0.8011    xx+yy+zz expectation -7.860512
0.6126    0.8168    xx+yy+zz expectation -7.887461
0.6126    0.8325    xx+yy+zz expectation -7.911568
0.6126    0.8482    xx+yy+zz expectation -7.932809
0.6126    0.8639    xx+yy+zz expectation -7.951164
0.6126    0.8796    xx+yy+zz expectation -7.966614
0.6126    0.8954    xx+yy+zz expectation -7.979145
0.6126    0.9111    xx+yy+zz expectation -7.988744
0.6126    0.9268    xx+yy+zz expectation -7.995402
0.6126    0.9425    xx+yy+zz expe

0.7383    0.8325    xx+yy+zz expectation -7.742471
0.7383    0.8482    xx+yy+zz expectation -7.774605
0.7383    0.8639    xx+yy+zz expectation -7.803646
0.7383    0.8796    xx+yy+zz expectation -7.829566
0.7383    0.8954    xx+yy+zz expectation -7.852338
0.7383    0.9111    xx+yy+zz expectation -7.871945
0.7383    0.9268    xx+yy+zz expectation -7.888361
0.7383    0.9425    xx+yy+zz expectation -7.901572
0.7383    0.9582    xx+yy+zz expectation -7.911567
0.7383    0.9739    xx+yy+zz expectation -7.918334
0.7383    0.9896    xx+yy+zz expectation -7.921865
0.7383    1.0053    xx+yy+zz expectation -7.922159
0.7383    1.021    xx+yy+zz expectation -7.919216
0.7383    1.0367    xx+yy+zz expectation -7.913041
0.7383    1.0524    xx+yy+zz expectation -7.903631
0.7383    1.0681    xx+yy+zz expectation -7.891006
0.7383    1.0838    xx+yy+zz expectation -7.875171
0.7383    1.0996    xx+yy+zz expectation -7.856145
0.754    0.7854    xx+yy+zz expectation -7.588265
0.754    0.8011    xx+yy+zz expec

In [14]:
print("alpha_opt=",np.around(alpha_opt,4),"  beta_opt=",np.around(beta_opt,4))
print()
print("Best estimate for GS energy after second iteration", np.around(expectation_opt,8))

alpha_opt= 0.6126   beta_opt= 0.9582

Best estimate for GS energy after second iteration -7.99986827


In [15]:
print("alpha_opt=",alpha_opt/np.pi,"pi,   beta_opt=",beta_opt/np.pi,"pi")

alpha_opt= 0.195 pi,   beta_opt= 0.305 pi


### compare with exact result for alpha, beta that give the GS with E=-8

In [16]:
print(np.arcsin(1/np.sqrt(3)),"   ",np.pi/2-np.arcsin(1/np.sqrt(3)))

0.6154797086703875     0.9553166181245091


## Now for $L=10$

In [17]:
length=10

qubits = cirq.LineQubit.range(length)

pauliX = cirq.X
pauliY = cirq.Y
pauliZ = cirq.Z

print(qubits)
print()

Heis_ham: cirq.ops.PauliSum = sum(pauliX(qubits[k - 1]) * pauliX(qubits[k]) 
+ pauliY(qubits[k - 1]) * pauliY(qubits[k]) + pauliZ(qubits[k - 1]) * pauliZ(qubits[k]) for k in range(length))
    
print("Hamiltonian =", Heis_ham)

[cirq.LineQubit(0), cirq.LineQubit(1), cirq.LineQubit(2), cirq.LineQubit(3), cirq.LineQubit(4), cirq.LineQubit(5), cirq.LineQubit(6), cirq.LineQubit(7), cirq.LineQubit(8), cirq.LineQubit(9)]

Hamiltonian = 1.000*X(0)*X(9)+1.000*Y(0)*Y(9)+1.000*Z(0)*Z(9)+1.000*X(0)*X(1)+1.000*Y(0)*Y(1)+1.000*Z(0)*Z(1)+1.000*X(1)*X(2)+1.000*Y(1)*Y(2)+1.000*Z(1)*Z(2)+1.000*X(2)*X(3)+1.000*Y(2)*Y(3)+1.000*Z(2)*Z(3)+1.000*X(3)*X(4)+1.000*Y(3)*Y(4)+1.000*Z(3)*Z(4)+1.000*X(4)*X(5)+1.000*Y(4)*Y(5)+1.000*Z(4)*Z(5)+1.000*X(5)*X(6)+1.000*Y(5)*Y(6)+1.000*Z(5)*Z(6)+1.000*X(6)*X(7)+1.000*Y(6)*Y(7)+1.000*Z(6)*Z(7)+1.000*X(7)*X(8)+1.000*Y(7)*Y(8)+1.000*Z(7)*Z(8)+1.000*X(8)*X(9)+1.000*Y(8)*Y(9)+1.000*Z(8)*Z(9)


In [18]:
circuit = cirq.Circuit()
print(circuit)

for i in range(length):
    if i % 2 == 0:
        circuit.append(cirq.H(qubits[i]))
        circuit.append(cirq.X(qubits[i]))
        circuit.append(cirq.CNOT(qubits[i],qubits[i+1]))
        circuit.append(cirq.X(qubits[i]))
        circuit.append(cirq.Z(qubits[i+1]))
    
print(circuit)


0: ───H───X───@───X───
              │
1: ───────────X───Z───

2: ───H───X───@───X───
              │
3: ───────────X───Z───

4: ───H───X───@───X───
              │
5: ───────────X───Z───

6: ───H───X───@───X───
              │
7: ───────────X───Z───

8: ───H───X───@───X───
              │
9: ───────────X───Z───


In [19]:
simulator = cirq.Simulator()
result = simulator.simulate(circuit, qubit_order=qubits)

expectation = Heis_ham.expectation_from_state_vector(
    result.final_state_vector,
    qubit_map={q: q.x for q in qubits})
print("xx+yy+zz expectation", expectation)

xx+yy+zz expectation (-14.9999982282119+0j)


## First iteration of optimization

In [20]:
alpha_opt=0
beta_opt=0
gamma_opt=0
delta_opt=0

expectation_opt=-3.0*length/2

num_step=8

for i1 in range(num_step+1):
    for i2 in range(num_step+1):
        for i3 in range(num_step+1):
            for i4 in range(num_step+1):
                alpha=np.pi*i1/(2*num_step)
                beta=np.pi*i2/(2*num_step)
                gamma=np.pi*i3/(2*num_step)
                delta=np.pi*i4/(2*num_step)

                circuit = cirq.Circuit()

                for i in range(length):
                    if i % 2 == 0:
                        circuit.append(cirq.H(qubits[i]))
                        circuit.append(cirq.X(qubits[i]))
                        circuit.append(cirq.CNOT(qubits[i],qubits[i+1]))
                        circuit.append(cirq.X(qubits[i]))
                        circuit.append(cirq.Z(qubits[i+1]))

                circuit.append(odd_Heis_layer(length, alpha))
                circuit.append(even_Heis_layer(length, beta))
                circuit.append(odd_Heis_layer(length, gamma))
                circuit.append(even_Heis_layer(length, delta))

                result = simulator.simulate(circuit, qubit_order=qubits)
                
                expectation = np.real(Heis_ham.expectation_from_state_vector(
                result.final_state_vector,
                    qubit_map={q: q.x for q in qubits}))
                # print(np.around(alpha,4), "  ", np.around(beta,4), "  ", np.around(gamma,4),"  ", np.around(delta,4), "   xx+yy+zz expectation", np.around(expectation,6))
                # print("xx+yy+zz expectation", expectation)

                if expectation < expectation_opt:
                    alpha_opt=alpha
                    beta_opt=beta
                    gamma_opt=gamma
                    delta_opt=delta
                    expectation_opt=expectation

In [21]:
print("alpha_opt=",np.around(alpha_opt,4),"  beta_opt=",np.around(beta_opt,4),
      "   gamma_opt=",np.around(gamma_opt,4),"  delta_opt=",np.around(delta_opt,4))
print()
print("Best estimate for GS energy after first iteration", np.around(expectation_opt,8))

alpha_opt= 0.7854   beta_opt= 1.5708    gamma_opt= 1.1781   delta_opt= 0.7854

Best estimate for GS energy after first iteration -17.58231714


## Second iteration of optimization

In [22]:
alpha_1=alpha_opt
beta_1=beta_opt
gamma_1=gamma_opt
delta_1=delta_opt

In [23]:
alpha_opt=0
beta_opt=0
gamma_opt=0
delta_opt=0

expectation_opt=-3.0*length/2

num_step=8

for i1 in range(num_step+1):
    for i2 in range(num_step+1):
        for i3 in range(num_step+1):
            for i4 in range(num_step+1):
                alpha=alpha_1 + np.pi*(i1-num_step/2)/(4*num_step)
                beta=beta_1 + np.pi*(i2-num_step/2)/(4*num_step)
                gamma=gamma_1 + np.pi*(i3-num_step/2)/(4*num_step)
                delta=delta_1 + np.pi*(i4-num_step/2)/(4*num_step)

                circuit = cirq.Circuit()

                for i in range(length):
                    if i % 2 == 0:
                        circuit.append(cirq.H(qubits[i]))
                        circuit.append(cirq.X(qubits[i]))
                        circuit.append(cirq.CNOT(qubits[i],qubits[i+1]))
                        circuit.append(cirq.X(qubits[i]))
                        circuit.append(cirq.Z(qubits[i+1]))

                circuit.append(odd_Heis_layer(length, alpha))
                circuit.append(even_Heis_layer(length, beta))
                circuit.append(odd_Heis_layer(length, gamma))
                circuit.append(even_Heis_layer(length, delta))

                result = simulator.simulate(circuit, qubit_order=qubits)

                expectation = np.real(Heis_ham.expectation_from_state_vector(
                result.final_state_vector,
                    qubit_map={q: q.x for q in qubits}))
                # print(np.around(alpha,4), "  ", np.around(beta,4), "  ", np.around(gamma,4),"  ", np.around(delta,4), "   xx+yy+zz expectation", np.around(expectation,6))
                # print("xx+yy+zz expectation", expectation)

                if expectation < expectation_opt:
                    alpha_opt=alpha
                    beta_opt=beta
                    gamma_opt=gamma
                    delta_opt=delta
                    expectation_opt=expectation

In [24]:
print("alpha_opt=",np.around(alpha_opt,4),"  beta_opt=",np.around(beta_opt,4),
      "   gamma_opt=",np.around(gamma_opt,4),"  delta_opt=",np.around(delta_opt,4))
print()
print("Best estimate for GS energy after second iteration", np.around(expectation_opt,8))

alpha_opt= 0.6872   beta_opt= 1.5708    gamma_opt= 1.0799   delta_opt= 0.7854

Best estimate for GS energy after second iteration -17.63943192


### compare with exact asymptotic behavior: E_L/L ~ (1 - 4 ln(2))

In [25]:
length=10
print("asymptotic prediction", length*(1 - 4*np.log(2)))

asymptotic prediction -17.725887222397812
